# Title of notebook

Brief 1-2 sentence description of notebook.

In [24]:
import glob
import re
import os

In [42]:
# Imports of all used packages and libraries
import numpy as np
import pandas as pd

## Inputs & Data

Explanation of each input and where it comes from.

In [34]:
# Inputs and Required data loading
# input varaible names are in all caps snake case
# Whenever an input changes or is used for processing 
# the vairables are all lower in snake case


TONE_TIMESTAMP_DF = pd.read_excel("../../rce_tone_timestamp.xlsx", index_col=0)
OUTPUT_DIR = r"./proc" # where data is saved should always be shown in the inputs

INPUT_DIR=glob.glob("/scratch/back_up/reward_competition_extention/proc/spike_sorting/*")

## Outputs

Describe each output that the notebook creates. 

- Is it a plot or is it data?

- How valuable is the output and why is it valuable or useful?

## Processing

Describe what is done to the data here and how inputs are manipulated to generate outputs. 

In [ ]:
# As much code and as many cells as required
# includes EDA and playing with data
# GO HAM!

# Ideally functions are defined here first and then data is processed using the functions

# function names are short and in snake case all lowercase
# a function name should be unique but does not have to describe the function
# doc strings describe functions not function names

def calc_bmi(weight, height):
    """
    This is a function that calculates BMI.
    it uses height and weight...etc.
    Meghan plz show us your docsctring format here.
    """
    bmi = weight/(height**2)
    return(bmi)


### Getting the subject IDs from the file name

In [6]:
all_trials_df = TONE_TIMESTAMP_DF.dropna(subset="condition").reset_index(drop=True)

In [7]:
all_trials_df.head()

time  state                                      recording_dir  \
0   9781115.0    1.0  20230612_101430_standard_comp_to_training_D1_s...   
1  12181113.0    1.0  20230612_101430_standard_comp_to_training_D1_s...   
2  14481111.0    1.0  20230612_101430_standard_comp_to_training_D1_s...   
3  16281110.0    1.0  20230612_101430_standard_comp_to_training_D1_s...   
4  17381106.0    1.0  20230612_101430_standard_comp_to_training_D1_s...   

                                      recording_file           din  \
0  20230612_101430_standard_comp_to_training_D1_s...  dio_ECU_Din1   
1  20230612_101430_standard_comp_to_training_D1_s...  dio_ECU_Din1   
2  20230612_101430_standard_comp_to_training_D1_s...  dio_ECU_Din1   
3  20230612_101430_standard_comp_to_training_D1_s...  dio_ECU_Din1   
4  20230612_101430_standard_comp_to_training_D1_s...  dio_ECU_Din1   

   time_stamp_index                                         video_file  \
0          982229.0  20230612_101430_standard_comp_to_training_D1_s...   
1         3382227.0  20230612_101430_standard_comp_to_training_D1_s...   
2         5682225.0  20230612_101430_standard_comp_to_training_D1_s...   
3         7482224.0  20230612_101430_standard_comp_to_training_D1_s...   
4         8582220.0  20230612_101430_standard_comp_to_training_D1_s...   

   video_frame  video_number    subject_info condition competition_closeness  \
0        980.0           2.0  1-3_t3b3L_box2       1.4           Subj 2 Only   
1       3376.0           2.0  1-3_t3b3L_box2       1.3           Subj 1 Only   
2       5671.0           2.0  1-3_t3b3L_box2       1.4           Subj 2 Only   
3       7468.0           2.0  1-3_t3b3L_box2       1.4           Subj 2 Only   
4       8566.0           2.0  1-3_t3b3L_box2       1.4           Subj 2 Only   

  Unnamed: 13  
0         NaN  
1         NaN  
2         NaN  
3         NaN  
4         NaN

- Original timestamps are based on ephys recordings at 20kHz. The LFP will be at 1kHz, so we will need to divide all the timestamps by 20

In [8]:
all_trials_df["resampled_index"] = all_trials_df["time_stamp_index"] // 20

In [9]:
all_trials_df["recording_dir"].unique()

array(['20230612_101430_standard_comp_to_training_D1_subj_1-4_and_1-3',
       '20230621_111240_standard_comp_to_omission_D5_subj_1-4_and_1-2',
       '20230620_114347_standard_comp_to_omission_D4_subj_1-2_and_1-1',
       '20230618_100636_standard_comp_to_omission_D2_subj_1-4_and_1-1',
       '20230619_115321_standard_comp_to_omission_D3_subj_1-2_and_1-4',
       '20221203_154800_omission_and_competition_subject_6_4_and_6_1',
       '20221215_145401_comp_amd_om_6_1_and_6_3',
       '20221202_134600_omission_and_competition_subject_6_1_and_6_2',
       '20221214_125409_om_and_comp_6_1_and_6_3'], dtype=object)

- Getting a list of all the subjects through the recording name

In [13]:
all_trials_df["all_subjects"] = all_trials_df["recording_dir"].apply(lambda x: ["{}.{}".format(tup[0],tup[1]) for tup in re.findall(r'(\d+)-(\d+)', x.replace("_", "-"))[1:]])

In [14]:
all_trials_df["all_subjects"].head()

0    [1.4, 1.3]
1    [1.4, 1.3]
2    [1.4, 1.3]
3    [1.4, 1.3]
4    [1.4, 1.3]
Name: all_subjects, dtype: object

- Getting the current subject of the recording through the ending of the recording name file

In [15]:
all_trials_df["subject_info"].head()

0    1-3_t3b3L_box2
1    1-3_t3b3L_box2
2    1-3_t3b3L_box2
3    1-3_t3b3L_box2
4    1-3_t3b3L_box2
Name: subject_info, dtype: object

In [16]:
all_trials_df["current_subject"] = all_trials_df["subject_info"].apply(lambda x: ".".join(x.replace("-","_").split("_")[:2]))

In [17]:
all_trials_df.head()

time  state                                      recording_dir  \
0   9781115.0    1.0  20230612_101430_standard_comp_to_training_D1_s...   
1  12181113.0    1.0  20230612_101430_standard_comp_to_training_D1_s...   
2  14481111.0    1.0  20230612_101430_standard_comp_to_training_D1_s...   
3  16281110.0    1.0  20230612_101430_standard_comp_to_training_D1_s...   
4  17381106.0    1.0  20230612_101430_standard_comp_to_training_D1_s...   

                                      recording_file           din  \
0  20230612_101430_standard_comp_to_training_D1_s...  dio_ECU_Din1   
1  20230612_101430_standard_comp_to_training_D1_s...  dio_ECU_Din1   
2  20230612_101430_standard_comp_to_training_D1_s...  dio_ECU_Din1   
3  20230612_101430_standard_comp_to_training_D1_s...  dio_ECU_Din1   
4  20230612_101430_standard_comp_to_training_D1_s...  dio_ECU_Din1   

   time_stamp_index                                         video_file  \
0          982229.0  20230612_101430_standard_comp_to_training_D1_s...   
1         3382227.0  20230612_101430_standard_comp_to_training_D1_s...   
2         5682225.0  20230612_101430_standard_comp_to_training_D1_s...   
3         7482224.0  20230612_101430_standard_comp_to_training_D1_s...   
4         8582220.0  20230612_101430_standard_comp_to_training_D1_s...   

   video_frame  video_number    subject_info condition competition_closeness  \
0        980.0           2.0  1-3_t3b3L_box2       1.4           Subj 2 Only   
1       3376.0           2.0  1-3_t3b3L_box2       1.3           Subj 1 Only   
2       5671.0           2.0  1-3_t3b3L_box2       1.4           Subj 2 Only   
3       7468.0           2.0  1-3_t3b3L_box2       1.4           Subj 2 Only   
4       8566.0           2.0  1-3_t3b3L_box2       1.4           Subj 2 Only   

  Unnamed: 13  resampled_index all_subjects current_subject  
0         NaN          49111.0   [1.4, 1.3]             1.3  
1         NaN         169111.0   [1.4, 1.3]             1.3  
2         NaN         284111.0   [1.4, 1.3]             1.3  
3         NaN         374111.0   [1.4, 1.3]             1.3  
4         NaN         429111.0   [1.4, 1.3]             1.3

- Labeling the trial as a winner or loser if the winner matches the subject id or not

In [18]:
all_trials_df["trial_outcome"] = all_trials_df.apply(
    lambda x: "win" if str(x["condition"]).strip() == str(x["current_subject"]) 
             else ("lose" if str(x["condition"]) in x["all_subjects"] 
                   else x["condition"]), axis=1)

In [19]:
all_trials_df.head()

time  state                                      recording_dir  \
0   9781115.0    1.0  20230612_101430_standard_comp_to_training_D1_s...   
1  12181113.0    1.0  20230612_101430_standard_comp_to_training_D1_s...   
2  14481111.0    1.0  20230612_101430_standard_comp_to_training_D1_s...   
3  16281110.0    1.0  20230612_101430_standard_comp_to_training_D1_s...   
4  17381106.0    1.0  20230612_101430_standard_comp_to_training_D1_s...   

                                      recording_file           din  \
0  20230612_101430_standard_comp_to_training_D1_s...  dio_ECU_Din1   
1  20230612_101430_standard_comp_to_training_D1_s...  dio_ECU_Din1   
2  20230612_101430_standard_comp_to_training_D1_s...  dio_ECU_Din1   
3  20230612_101430_standard_comp_to_training_D1_s...  dio_ECU_Din1   
4  20230612_101430_standard_comp_to_training_D1_s...  dio_ECU_Din1   

   time_stamp_index                                         video_file  \
0          982229.0  20230612_101430_standard_comp_to_training_D1_s...   
1         3382227.0  20230612_101430_standard_comp_to_training_D1_s...   
2         5682225.0  20230612_101430_standard_comp_to_training_D1_s...   
3         7482224.0  20230612_101430_standard_comp_to_training_D1_s...   
4         8582220.0  20230612_101430_standard_comp_to_training_D1_s...   

   video_frame  video_number    subject_info condition competition_closeness  \
0        980.0           2.0  1-3_t3b3L_box2       1.4           Subj 2 Only   
1       3376.0           2.0  1-3_t3b3L_box2       1.3           Subj 1 Only   
2       5671.0           2.0  1-3_t3b3L_box2       1.4           Subj 2 Only   
3       7468.0           2.0  1-3_t3b3L_box2       1.4           Subj 2 Only   
4       8566.0           2.0  1-3_t3b3L_box2       1.4           Subj 2 Only   

  Unnamed: 13  resampled_index all_subjects current_subject trial_outcome  
0         NaN          49111.0   [1.4, 1.3]             1.3          lose  
1         NaN         169111.0   [1.4, 1.3]             1.3           win  
2         NaN         284111.0   [1.4, 1.3]             1.3          lose  
3         NaN         374111.0   [1.4, 1.3]             1.3          lose  
4         NaN         429111.0   [1.4, 1.3]             1.3          lose

In [20]:
all_trials_df

time  state                                      recording_dir  \
0     9781115.0    1.0  20230612_101430_standard_comp_to_training_D1_s...   
1    12181113.0    1.0  20230612_101430_standard_comp_to_training_D1_s...   
2    14481111.0    1.0  20230612_101430_standard_comp_to_training_D1_s...   
3    16281110.0    1.0  20230612_101430_standard_comp_to_training_D1_s...   
4    17381106.0    1.0  20230612_101430_standard_comp_to_training_D1_s...   
..          ...    ...                                                ...   
636  56250471.0    1.0            20221214_125409_om_and_comp_6_1_and_6_3   
637  58050469.0    1.0            20221214_125409_om_and_comp_6_1_and_6_3   
638  59950467.0    1.0            20221214_125409_om_and_comp_6_1_and_6_3   
639  62350467.0    1.0            20221214_125409_om_and_comp_6_1_and_6_3   
640  63950466.0    1.0            20221214_125409_om_and_comp_6_1_and_6_3   

                                        recording_file           din  \
0    20230612_101430_standard_comp_to_training_D1_s...  dio_ECU_Din1   
1    20230612_101430_standard_comp_to_training_D1_s...  dio_ECU_Din1   
2    20230612_101430_standard_comp_to_training_D1_s...  dio_ECU_Din1   
3    20230612_101430_standard_comp_to_training_D1_s...  dio_ECU_Din1   
4    20230612_101430_standard_comp_to_training_D1_s...  dio_ECU_Din1   
..                                                 ...           ...   
636  20221214_125409_om_and_comp_6_1_top_1_base_2_v...  dio_ECU_Din1   
637  20221214_125409_om_and_comp_6_1_top_1_base_2_v...  dio_ECU_Din1   
638  20221214_125409_om_and_comp_6_1_top_1_base_2_v...  dio_ECU_Din1   
639  20221214_125409_om_and_comp_6_1_top_1_base_2_v...  dio_ECU_Din1   
640  20221214_125409_om_and_comp_6_1_top_1_base_2_v...  dio_ECU_Din1   

     time_stamp_index                                         video_file  \
0            982229.0  20230612_101430_standard_comp_to_training_D1_s...   
1           3382227.0  20230612_101430_standard_comp_to_training_D1_s...   
2           5682225.0  20230612_101430_standard_comp_to_training_D1_s...   
3           7482224.0  20230612_101430_standard_comp_to_training_D1_s...   
4           8582220.0  20230612_101430_standard_comp_to_training_D1_s...   
..                ...                                                ...   
636        53298568.0  20221214_125409_om_and_comp_6_1_and_6_3.1.vide...   
637        55098566.0  20221214_125409_om_and_comp_6_1_and_6_3.1.vide...   
638        56998564.0  20221214_125409_om_and_comp_6_1_and_6_3.1.vide...   
639        59398564.0  20221214_125409_om_and_comp_6_1_and_6_3.1.vide...   
640        60998563.0  20221214_125409_om_and_comp_6_1_and_6_3.1.vide...   

     video_frame  video_number             subject_info condition  \
0          980.0           2.0           1-3_t3b3L_box2       1.4   
1         3376.0           2.0           1-3_t3b3L_box2       1.3   
2         5671.0           2.0           1-3_t3b3L_box2       1.4   
3         7468.0           2.0           1-3_t3b3L_box2       1.4   
4         8566.0           2.0           1-3_t3b3L_box2       1.4   
..           ...           ...                      ...       ...   
636      60112.0           1.0  6_1_top_1_base_2_vs_6_3       6.3   
637      62355.0           1.0  6_1_top_1_base_2_vs_6_3       6.3   
638      64724.0           1.0  6_1_top_1_base_2_vs_6_3       6.1   
639      67716.0           1.0  6_1_top_1_base_2_vs_6_3       6.3   
640      69710.0           1.0  6_1_top_1_base_2_vs_6_3       6.3   

    competition_closeness Unnamed: 13  resampled_index all_subjects  \
0             Subj 2 Only         NaN          49111.0   [1.4, 1.3]   
1             Subj 1 Only         NaN         169111.0   [1.4, 1.3]   
2             Subj 2 Only         NaN         284111.0   [1.4, 1.3]   
3             Subj 2 Only         NaN         374111.0   [1.4, 1.3]   
4             Subj 2 Only         NaN         429111.0   [1.4, 1.3]   
..                    ...         ...              ..

In [21]:
CVD_DF

NameError: name 'CVD_DF' is not defined

In [ ]:
DeepnoteChart(CVD_DF, """{"layer":[{"layer":[{"mark":{"clip":true,"type":"circle","tooltip":true},"encoding":{"x":{"sort":null,"type":"quantitative","field":"Height_(cm)","scale":{"type":"linear","zero":false},"format":{"type":"default","decimals":null},"formatType":"numberFormatFromNumberType"},"y":{"sort":null,"type":"quantitative","field":"Weight_(kg)","scale":{"type":"linear","zero":false},"format":{"type":"default","decimals":null},"formatType":"numberFormatFromNumberType"},"color":{"sort":null,"type":"nominal","field":"Diabetes","scale":{"scheme":"tableau10"}}}}]}],"title":"","config":{"legend":{}},"$schema":"https://vega.github.io/schema/vega-lite/v5.json","encoding":{}}""")

# Reading in Phy

- Which unit the spike came from

In [30]:
recording_dir

'/scratch/back_up/reward_competition_extention/proc/spike_sorting/20230613_105657_standard_comp_to_training_D2_subj_1-1_t1b2L_box1_merged.rec'

In [44]:
recording_to_spike_clusters = {}
for recording_dir in INPUT_DIR:
    try:
        recording_basename = os.path.basename(recording_dir).strip(".rec")
        file_path = os.path.join(recording_dir, "phy", "spike_clusters.npy")
        recording_to_spike_clusters[recording_basename] = np.load(file_path)
    except Exception as e:
        print(e)

[Errno 2] No such file or directory: '/scratch/back_up/reward_competition_extention/proc/spike_sorting/old/phy/spike_clusters.npy'
[Errno 2] No such file or directory: '/scratch/back_up/reward_competition_extention/proc/spike_sorting/20230623_114932_standard_comp_to_both_rewarded_D2_subj_1-1_t1b2L_box1_merged.rec/phy/spike_clusters.npy'
[Errno 2] No such file or directory: '/scratch/back_up/reward_competition_extention/proc/spike_sorting/20230623_114932_standard_comp_to_both_rewarded_D2_subj_1-4_t13b3L_box1_merged.rec/phy/spike_clusters.npy'


- The classification of each unit

In [46]:
recording_to_cluster_info = {}
for recording_dir in INPUT_DIR:
    try:
        recording_basename = os.path.basename(recording_dir).strip(".rec")
        file_path = os.path.join(recording_dir, "phy", "cluster_info.tsv")
        recording_to_cluster_info[recording_basename] = pd.read_csv(file_path, sep="\t")
    except Exception as e:
        print(e)

[Errno 2] No such file or directory: '/scratch/back_up/reward_competition_extention/proc/spike_sorting/20221125_152723_competition_subject_6_1_top_3_base_2_merged.rec/phy/cluster_info.tsv'
[Errno 2] No such file or directory: '/scratch/back_up/reward_competition_extention/proc/spike_sorting/20230616_111904_standard_comp_to_training_D4_subj_1-4_t4b3L_box1_merged.rec/phy/cluster_info.tsv'
[Errno 2] No such file or directory: '/scratch/back_up/reward_competition_extention/proc/spike_sorting/20230612_101430_standard_comp_to_training_D1_subj_1-4_t4b2L_box1_merged.rec/phy/cluster_info.tsv'
[Errno 2] No such file or directory: '/scratch/back_up/reward_competition_extention/proc/spike_sorting/20221202_134600_omission_and_competition_subject_6_1_top_2_base_3_merged.rec/phy/cluster_info.tsv'
[Errno 2] No such file or directory: '/scratch/back_up/reward_competition_extention/proc/spike_sorting/20230622_110832_standard_comp_to_both_rewarded_D1_subj_1-1_t1b3L_box1_merged.rec/phy/cluster_info.tsv'
[

In [49]:
recording_to_cluster_info["20230618_100636_standard_comp_to_omission_D2_subj_1_4_t4b3L_box1_merged"]

cluster_id        amp  ch  channel_group  depth        fr  group  \
0            0   9.704487   0              0    0.0  8.615203    mua   
1            1  15.160955   0              0    0.0  2.351562   good   
2            2  10.994174   1              0   20.0  0.631263   good   
3            3   9.616855   1              0   20.0  5.323891    mua   
4            4  13.022879   2              0   40.0  9.569241   good   
5            5   9.269071   2              0   40.0  2.569370    mua   
6            7   8.466800   2              0   40.0  2.642555   good   
7            8   9.198713   3              0   60.0  0.217516    mua   
8            9  12.508228   3              0   60.0  1.605419   good   
9           13  10.283003  10              0  200.0  1.223162    mua   
10          14  11.179998  10              0  200.0  1.098951    mua   
11          15  12.219653  10              0  200.0  1.143854    mua   
12          16  14.966177  10              0  200.0  1.574803    mua   
13          17  11.075341  14              0  280.0  0.805625    mua   
14          18  13.106446  14              0  280.0  2.297038   good   
15          19  13.435120  15              0  300.0  0.503261    mua   
16          20   7.342390  20              0  400.0  0.219265    mua   
17          21  10.664793  21              0  420.0  0.605604  noise   
18          22  10.601178  21              0  420.0  2.911680    mua   
19          23   9.276388  22              0  440.0  0.127419    mua   
20          24  32.874237  23              0  460.0  0.522213    mua   
21          25  19.984566  24              0  480.0  2.390050   good   
22          26  10.468862  24              0  480.0  2.947253    mua   
23          30   9.754337   2              0   40.0  1.114113   good   
24          31   9.754337   2              0   40.0  1.758788    mua   
25          38  14.402934   6              0  120.0  7.804621   good   
26          39  14.402934   6              0  120.0  0.838282    mua   
27          42  10.973118   6              0  120.0  3.327176   good   
28          44  10.973118   6              0  120.0  0.308779    mua   
29          45  10.973118   6              0  120.0  0.006415  noise   
30          46   9.491500   7              0  140.0  0.372343    mua   
31          48   9.491500   7              0  140.0  0.608811   good   
32          49   9.491500   7              0  140.0  0.017786  noise   
33          56  10.401958  31              0  620.0  1.577719    mua   
34          57  10.401958  31              0  620.0  0.081641    mua   
35          58  12.047513  31              0  620.0  1.082623    mua   
36          59  12.047513  31              0  620.0  0.015454  noise   
37          60  13.630511  30              0  600.0  2.587448    mua   
38          61  13.630511  30              0  600.0  0.065313  noise   

    n_spikes  sh  si_unit_id  
0      29547   0           1  
1       8065   0           2  
2       2165   0           3  
3      18259   0           4  
4      32819   0           5  
5       8812   0           6  
6       9063   0           8  
7        746   0           9  
8       5506   0          10  
9       4195   0          14  
10      3769   0          15  
11      3923   0          16  
12      5401   0          17  
13      2763   0          18  
14      7878   0          19  
15      1726   0          20  
16       752   0          22  
17      2077   0          23  
18      9986   0          24  
19       437   0          25  
20      1791   0          26  
21      8197   0          27  
22     10108   0          28  
23      3821   0           7  
24      6032   0           7  
25     26767   0          11  
26      2875   0          11  
27     11411   0          12  
28      1059   0          12  
29        22   0          12  
30      1277   0          13  
31      2088   0          13  
32        61   0          13  
33      5411   0          31  
34       280   0          31  
35     

In [50]:
recording_to_cluster_info_df = pd.concat(recording_to_cluster_info, names=['recording_name']).reset_index(level=1, drop=True).reset_index()


In [51]:
recording_to_cluster_info_df

recording_name  cluster_id        amp  \
0    20230618_100636_standard_comp_to_omission_D2_s...           0   9.704487   
1    20230618_100636_standard_comp_to_omission_D2_s...           1  15.160955   
2    20230618_100636_standard_comp_to_omission_D2_s...           2  10.994174   
3    20230618_100636_standard_comp_to_omission_D2_s...           3   9.616855   
4    20230618_100636_standard_comp_to_omission_D2_s...           4  13.022879   
..                                                 ...         ...        ...   
326  20230619_115321_standard_comp_to_omission_D3_s...          82   9.249042   
327  20230619_115321_standard_comp_to_omission_D3_s...          87  11.722415   
328  20230619_115321_standard_comp_to_omission_D3_s...          88  11.722415   
329  20230619_115321_standard_comp_to_omission_D3_s...          89  13.939378   
330  20230619_115321_standard_comp_to_omission_D3_s...          90   8.631100   

     ch  channel_group  depth        fr  group  n_spikes  sh  si_unit_id  
0     0            0.0    0.0  8.615203    mua     29547   0         1.0  
1     0            0.0    0.0  2.351562   good      8065   0         2.0  
2     1            0.0   20.0  0.631263   good      2165   0         3.0  
3     1            0.0   20.0  5.323891    mua     18259   0         4.0  
4     2            0.0   40.0  9.569241   good     32819   0         5.0  
..   ..            ...    ...       ...    ...       ...  ..         ...  
326   8            0.0  160.0  0.001942  noise         4   0        22.0  
327  10            0.0  200.0  4.377602   good      9015   0        28.0  
328  10            0.0  200.0  0.190352  noise       392   0        28.0  
329  13            0.0  260.0  1.063930   good      2191   0        32.0  
330  14            0.0  280.0  1.450946   good      2988   0        36.0  

[331 rows x 11 columns]

- Filtering for the good units

In [52]:
good_unit_cluster_info_df = recording_to_cluster_info_df[recording_to_cluster_info_df["group"] == "good"]

In [53]:
good_unit_cluster_info_df

recording_name  cluster_id        amp  \
1    20230618_100636_standard_comp_to_omission_D2_s...           1  15.160955   
2    20230618_100636_standard_comp_to_omission_D2_s...           2  10.994174   
4    20230618_100636_standard_comp_to_omission_D2_s...           4  13.022879   
6    20230618_100636_standard_comp_to_omission_D2_s...           7   8.466800   
8    20230618_100636_standard_comp_to_omission_D2_s...           9  12.508228   
..                                                 ...         ...        ...   
319  20230619_115321_standard_comp_to_omission_D3_s...          73  12.354398   
323  20230619_115321_standard_comp_to_omission_D3_s...          77   7.057085   
327  20230619_115321_standard_comp_to_omission_D3_s...          87  11.722415   
329  20230619_115321_standard_comp_to_omission_D3_s...          89  13.939378   
330  20230619_115321_standard_comp_to_omission_D3_s...          90   8.631100   

     ch  channel_group  depth        fr group  n_spikes  sh  si_unit_id  
1     0            0.0    0.0  2.351562  good      8065   0         2.0  
2     1            0.0   20.0  0.631263  good      2165   0         3.0  
4     2            0.0   40.0  9.569241  good     32819   0         5.0  
6     2            0.0   40.0  2.642555  good      9063   0         8.0  
8     3            0.0   60.0  1.605419  good      5506   0        10.0  
..   ..            ...    ...       ...   ...       ...  ..         ...  
319   2            0.0   40.0  2.966960  good      6110   0        10.0  
323   7            0.0  140.0  0.553574  good      1140   0        21.0  
327  10            0.0  200.0  4.377602  good      9015   0        28.0  
329  13            0.0  260.0  1.063930  good      2191   0        32.0  
330  14            0.0  280.0  1.450946  good      2988   0        36.0  

[104 rows x 11 columns]

In [54]:
good_unit_cluster_info_df["recording_name"].unique()

array(['20230618_100636_standard_comp_to_omission_D2_subj_1_4_t4b3L_box1_merged',
       '20230618_100636_standard_comp_to_omission_D2_subj_1_1_t1b2L_box2_merged',
       '20230620_114347_standard_comp_to_omission_D4_subj_1-1_t1b2L_box_2_merged',
       '20221122_161341_omission_subject_6_1_top_4_base_2',
       '20230620_114347_standard_comp_to_omission_D4_subj_1-2_t3b3L_box_1_merged',
       '20230619_115321_standard_comp_to_omission_D3_subj_1-4_t3b3L_box2_merged'],
      dtype=object)

In [63]:
recording_to_good_unit_ids = good_unit_cluster_info_df.groupby('recording_name')['cluster_id'].apply(list).to_dict()


In [64]:
recording_to_good_unit_ids

{'20221122_161341_omission_subject_6_1_top_4_base_2': [3, 5],
 '20230618_100636_standard_comp_to_omission_D2_subj_1_1_t1b2L_box2_merged': [1,
  3,
  4,
  6,
  7,
  8,
  10,
  14,
  20,
  29,
  38,
  40,
  48,
  55,
  58,
  64],
 '20230618_100636_standard_comp_to_omission_D2_subj_1_4_t4b3L_box1_merged': [1,
  2,
  4,
  7,
  9,
  18,
  25,
  30,
  38,
  42,
  48],
 '20230619_115321_standard_comp_to_omission_D3_subj_1-4_t3b3L_box2_merged': [1,
  5,
  9,
  10,
  12,
  14,
  15,
  16,
  18,
  25,
  28,
  29,
  37,
  40,
  44,
  52,
  57,
  58,
  63,
  73,
  77,
  87,
  89,
  90],
 '20230620_114347_standard_comp_to_omission_D4_subj_1-1_t1b2L_box_2_merged': [0,
  2,
  4,
  5,
  8,
  18,
  20,
  22,
  26,
  30,
  32,
  34,
  41,
  42,
  48],
 '20230620_114347_standard_comp_to_omission_D4_subj_1-2_t3b3L_box_1_merged': [2,
  3,
  8,
  9,
  19,
  20,
  23,
  27,
  38,
  40,
  41,
  42,
  45,
  46,
  48,
  49,
  50,
  51,
  53,
  54,
  58,
  68,
  70,
  72,
  78,
  84,
  86,
  91,
  95,
  102,
  1

- The times that all the spikes happened

In [57]:
recording_to_spike_times = {}
for recording_dir in INPUT_DIR:
    try:
        recording_basename = os.path.basename(recording_dir).strip(".rec")
        file_path = os.path.join(recording_dir, "phy", "spike_times.npy")
        recording_to_spike_times[recording_basename] = np.load(file_path)
    except Exception as e:
        print(e)

[Errno 2] No such file or directory: '/scratch/back_up/reward_competition_extention/proc/spike_sorting/old/phy/spike_times.npy'
[Errno 2] No such file or directory: '/scratch/back_up/reward_competition_extention/proc/spike_sorting/20230623_114932_standard_comp_to_both_rewarded_D2_subj_1-1_t1b2L_box1_merged.rec/phy/spike_times.npy'
[Errno 2] No such file or directory: '/scratch/back_up/reward_competition_extention/proc/spike_sorting/20230623_114932_standard_comp_to_both_rewarded_D2_subj_1-4_t13b3L_box1_merged.rec/phy/spike_times.npy'


- Getting a list of the IDs that were good from the list of unit ids for all the firings

In [59]:
recording_to_spike_clusters

{'20221125_152723_competition_subject_6_1_top_3_base_2_merged': array([[15],
        [ 0],
        [25],
        ...,
        [ 1],
        [21],
        [22]]),
 '20230616_111904_standard_comp_to_training_D4_subj_1-4_t4b3L_box1_merged': array([[ 5],
        [33],
        [43],
        ...,
        [36],
        [35],
        [36]]),
 '20230618_100636_standard_comp_to_omission_D2_subj_1_4_t4b3L_box1_merged': array([60, 60, 60, ...,  1,  4, 42], dtype=int32),
 '20230612_101430_standard_comp_to_training_D1_subj_1-4_t4b2L_box1_merged': array([[16],
        [ 4],
        [27],
        ...,
        [15],
        [ 3],
        [ 8]]),
 '20221202_134600_omission_and_competition_subject_6_1_top_2_base_3_merged': array([[16],
        [ 1],
        [18],
        ...,
        [ 1],
        [ 7],
        [14]]),
 '20230622_110832_standard_comp_to_both_rewarded_D1_subj_1-1_t1b3L_box1_merged': array([[ 9],
        [46],
        [42],
        ...,
        [54],
        [49],
        [54]]),
 '2023061

In [65]:
recording_to_good_unit_ids

{'20221122_161341_omission_subject_6_1_top_4_base_2': [3, 5],
 '20230618_100636_standard_comp_to_omission_D2_subj_1_1_t1b2L_box2_merged': [1,
  3,
  4,
  6,
  7,
  8,
  10,
  14,
  20,
  29,
  38,
  40,
  48,
  55,
  58,
  64],
 '20230618_100636_standard_comp_to_omission_D2_subj_1_4_t4b3L_box1_merged': [1,
  2,
  4,
  7,
  9,
  18,
  25,
  30,
  38,
  42,
  48],
 '20230619_115321_standard_comp_to_omission_D3_subj_1-4_t3b3L_box2_merged': [1,
  5,
  9,
  10,
  12,
  14,
  15,
  16,
  18,
  25,
  28,
  29,
  37,
  40,
  44,
  52,
  57,
  58,
  63,
  73,
  77,
  87,
  89,
  90],
 '20230620_114347_standard_comp_to_omission_D4_subj_1-1_t1b2L_box_2_merged': [0,
  2,
  4,
  5,
  8,
  18,
  20,
  22,
  26,
  30,
  32,
  34,
  41,
  42,
  48],
 '20230620_114347_standard_comp_to_omission_D4_subj_1-2_t3b3L_box_1_merged': [2,
  3,
  8,
  9,
  19,
  20,
  23,
  27,
  38,
  40,
  41,
  42,
  45,
  46,
  48,
  49,
  50,
  51,
  53,
  54,
  58,
  68,
  70,
  72,
  78,
  84,
  86,
  91,
  95,
  102,
  1

In [68]:
recording_to_good_unit_mask = {recording: np.isin(spike_clusters, recording_to_good_unit_ids[recording]) for recording, spike_clusters in recording_to_spike_clusters.items() if recording in recording_to_good_unit_ids}


In [69]:
recording_to_good_unit_all_ids = {recording: recording_to_spike_clusters[recording][good_unit_mask] for recording, good_unit_mask in recording_to_good_unit_mask.items()}


- Getting the time that the good units fired

In [71]:
recording_to_good_unit_times = {recording: recording_to_spike_times[recording][good_unit_mask] for recording, good_unit_mask in recording_to_good_unit_mask.items()}


# Labeling before or after

In [77]:
all_trials_df = all_trials_df[all_trials_df["recording_file"].isin(recording_to_good_unit_times.keys())].reset_index(drop=True)

In [78]:
all_trials_df

time  state                                      recording_dir  \
0     8260195.0    1.0  20230620_114347_standard_comp_to_omission_D4_s...   
1    10060217.0    1.0  20230620_114347_standard_comp_to_omission_D4_s...   
2    11160233.0    1.0  20230620_114347_standard_comp_to_omission_D4_s...   
3    12160245.0    1.0  20230620_114347_standard_comp_to_omission_D4_s...   
4    14060266.0    1.0  20230620_114347_standard_comp_to_omission_D4_s...   
..          ...    ...                                                ...   
324  37719707.0    1.0  20230619_115321_standard_comp_to_omission_D3_s...   
325  38819710.0    1.0  20230619_115321_standard_comp_to_omission_D3_s...   
326  40119707.0    1.0  20230619_115321_standard_comp_to_omission_D3_s...   
327  41219709.0    1.0  20230619_115321_standard_comp_to_omission_D3_s...   
328  42219708.0    1.0  20230619_115321_standard_comp_to_omission_D3_s...   

                                        recording_file           din  \
0    20230620_114347_standard_comp_to_omission_D4_s...  dio_ECU_Din1   
1    20230620_114347_standard_comp_to_omission_D4_s...  dio_ECU_Din1   
2    20230620_114347_standard_comp_to_omission_D4_s...  dio_ECU_Din1   
3    20230620_114347_standard_comp_to_omission_D4_s...  dio_ECU_Din1   
4    20230620_114347_standard_comp_to_omission_D4_s...  dio_ECU_Din1   
..                                                 ...           ...   
324  20230619_115321_standard_comp_to_omission_D3_s...  dio_ECU_Din1   
325  20230619_115321_standard_comp_to_omission_D3_s...  dio_ECU_Din1   
326  20230619_115321_standard_comp_to_omission_D3_s...  dio_ECU_Din1   
327  20230619_115321_standard_comp_to_omission_D3_s...  dio_ECU_Din1   
328  20230619_115321_standard_comp_to_omission_D3_s...  dio_ECU_Din1   

     time_stamp_index                                         video_file  \
0           5757314.0  20230620_114347_standard_comp_to_omission_D4_s...   
1           7557336.0  20230620_114347_standard_comp_to_omission_D4_s...   
2           8657352.0  20230620_114347_standard_comp_to_omission_D4_s...   
3           9657364.0  20230620_114347_standard_comp_to_omission_D4_s...   
4          11557385.0  20230620_114347_standard_comp_to_omission_D4_s...   
..                ...                                                ...   
324        36077451.0  20230619_115321_standard_comp_to_omission_D3_s...   
325        37177454.0  20230619_115321_standard_comp_to_omission_D3_s...   
326        38477451.0  20230619_115321_standard_comp_to_omission_D3_s...   
327        39577453.0  20230619_115321_standard_comp_to_omission_D3_s...   
328        40577452.0  20230619_115321_standard_comp_to_omission_D3_s...   

     video_frame  video_number     subject_info condition  \
0         5745.0           2.0  1-1_t1b2L_box_2       1.2   
1         7542.0           2.0  1-1_t1b2L_box_2       1.1   
2         8640.0           2.0  1-1_t1b2L_box_2       1.1   
3         9638.0           2.0  1-1_t1b2L_box_2       1.1   
4        11535.0           2.0  1-1_t1b2L_box_2       1.1   
..           ...           ...              ...       ...   
324      36009.0           4.0   1-4_t3b3L_box2  rewarded   
325      37107.0           4.0   1-4_t3b3L_box2  rewarded   
326      38405.0           4.0   1-4_t3b3L_box2  rewarded   
327      39503.0           4.0   1-4_t3b3L_box2  rewarded   
328      40500.0           4.0   1-4_t3b3L_box2  rewarded   

      competition_closeness                Unnamed: 13  resampled_index  \
0    Subj 2 blocking Subj 1                        NaN         287865.0   
1               Subj 1 Only                        NaN         377866.0   
2        Subj 1 then Subj 2  1.1 still at port at 8791         432867.0   
3               Subj 1 Only                        NaN         482868.0   
4               Subj 1 Only                        NaN         577869.0   
..                      ...                        ...              ...   
324                     NaN                       

# Calculating the firing rate

In [85]:
all_trials_df.columns

Index(['time', 'state', 'recording_dir', 'recording_file', 'din',
       'time_stamp_index', 'video_file', 'video_frame', 'video_number',
       'subject_info', 'condition', 'competition_closeness', 'Unnamed: 13',
       'resampled_index', 'all_subjects', 'current_subject', 'trial_outcome'],
      dtype='object')

In [87]:
all_trials_df

time  state                                      recording_dir  \
0     8260195.0    1.0  20230620_114347_standard_comp_to_omission_D4_s...   
1    10060217.0    1.0  20230620_114347_standard_comp_to_omission_D4_s...   
2    11160233.0    1.0  20230620_114347_standard_comp_to_omission_D4_s...   
3    12160245.0    1.0  20230620_114347_standard_comp_to_omission_D4_s...   
4    14060266.0    1.0  20230620_114347_standard_comp_to_omission_D4_s...   
..          ...    ...                                                ...   
324  37719707.0    1.0  20230619_115321_standard_comp_to_omission_D3_s...   
325  38819710.0    1.0  20230619_115321_standard_comp_to_omission_D3_s...   
326  40119707.0    1.0  20230619_115321_standard_comp_to_omission_D3_s...   
327  41219709.0    1.0  20230619_115321_standard_comp_to_omission_D3_s...   
328  42219708.0    1.0  20230619_115321_standard_comp_to_omission_D3_s...   

                                        recording_file           din  \
0    20230620_114347_standard_comp_to_omission_D4_s...  dio_ECU_Din1   
1    20230620_114347_standard_comp_to_omission_D4_s...  dio_ECU_Din1   
2    20230620_114347_standard_comp_to_omission_D4_s...  dio_ECU_Din1   
3    20230620_114347_standard_comp_to_omission_D4_s...  dio_ECU_Din1   
4    20230620_114347_standard_comp_to_omission_D4_s...  dio_ECU_Din1   
..                                                 ...           ...   
324  20230619_115321_standard_comp_to_omission_D3_s...  dio_ECU_Din1   
325  20230619_115321_standard_comp_to_omission_D3_s...  dio_ECU_Din1   
326  20230619_115321_standard_comp_to_omission_D3_s...  dio_ECU_Din1   
327  20230619_115321_standard_comp_to_omission_D3_s...  dio_ECU_Din1   
328  20230619_115321_standard_comp_to_omission_D3_s...  dio_ECU_Din1   

     time_stamp_index                                         video_file  \
0           5757314.0  20230620_114347_standard_comp_to_omission_D4_s...   
1           7557336.0  20230620_114347_standard_comp_to_omission_D4_s...   
2           8657352.0  20230620_114347_standard_comp_to_omission_D4_s...   
3           9657364.0  20230620_114347_standard_comp_to_omission_D4_s...   
4          11557385.0  20230620_114347_standard_comp_to_omission_D4_s...   
..                ...                                                ...   
324        36077451.0  20230619_115321_standard_comp_to_omission_D3_s...   
325        37177454.0  20230619_115321_standard_comp_to_omission_D3_s...   
326        38477451.0  20230619_115321_standard_comp_to_omission_D3_s...   
327        39577453.0  20230619_115321_standard_comp_to_omission_D3_s...   
328        40577452.0  20230619_115321_standard_comp_to_omission_D3_s...   

     video_frame  video_number     subject_info condition  \
0         5745.0           2.0  1-1_t1b2L_box_2       1.2   
1         7542.0           2.0  1-1_t1b2L_box_2       1.1   
2         8640.0           2.0  1-1_t1b2L_box_2       1.1   
3         9638.0           2.0  1-1_t1b2L_box_2       1.1   
4        11535.0           2.0  1-1_t1b2L_box_2       1.1   
..           ...           ...              ...       ...   
324      36009.0           4.0   1-4_t3b3L_box2  rewarded   
325      37107.0           4.0   1-4_t3b3L_box2  rewarded   
326      38405.0           4.0   1-4_t3b3L_box2  rewarded   
327      39503.0           4.0   1-4_t3b3L_box2  rewarded   
328      40500.0           4.0   1-4_t3b3L_box2  rewarded   

      competition_closeness                Unnamed: 13  resampled_index  \
0    Subj 2 blocking Subj 1                        NaN         287865.0   
1               Subj 1 Only                        NaN         377866.0   
2        Subj 1 then Subj 2  1.1 still at port at 8791         432867.0   
3               Subj 1 Only                        NaN         482868.0   
4               Subj 1 Only                        NaN         577869.0   
..                      ...                        ...              ...   
324                     NaN                       

In [90]:
all_trials_df["time_stamp_index"] = all_trials_df["time_stamp_index"].astype(int)

In [96]:
grouped_trials_df = all_trials_df.groupby(["recording_file", "current_subject", "video_number"]).agg({
    'time_stamp_index': list,
    'trial_outcome': list,
    'competition_closeness': list}).reset_index()

In [97]:
grouped_trials_df

recording_file current_subject  \
0  20230618_100636_standard_comp_to_omission_D2_s...             1.1   
1  20230618_100636_standard_comp_to_omission_D2_s...             1.1   
2  20230618_100636_standard_comp_to_omission_D2_s...             1.4   
3  20230618_100636_standard_comp_to_omission_D2_s...             1.4   
4  20230619_115321_standard_comp_to_omission_D3_s...             1.4   
5  20230620_114347_standard_comp_to_omission_D4_s...             1.1   
6  20230620_114347_standard_comp_to_omission_D4_s...             1.1   
7  20230620_114347_standard_comp_to_omission_D4_s...             1.2   
8  20230620_114347_standard_comp_to_omission_D4_s...             1.2   

   video_number                                   time_stamp_index  \
0           1.0  [1099250, 3499256, 5799251, 7599250, 8699250, ...   
1           2.0  [1099250, 3499256, 5799251, 7599250, 8699250, ...   
2           1.0  [1099250, 3499256, 5799251, 7599250, 8699250, ...   
3           2.0  [1099250, 3499256, 5799251, 7599250, 8699250, ...   
4           4.0  [1277472, 3577468, 5377470, 6477469, 7477469, ...   
5           1.0  [5757314, 7557336, 8657352, 9657364, 11557385,...   
6           2.0  [5757314, 7557336, 8657352, 9657364, 11557385,...   
7           1.0  [5757314, 7557336, 8657352, 9657364, 11557385,...   
8           2.0  [5757314, 7557336, 8657352, 9657364, 11557385,...   

                                       trial_outcome  \
0  [lose, win, win, lose, win, lose, lose, lose, ...   
1  [lose, win, win, lose, win, lose, lose, lose, ...   
2  [win, lose, lose, win, lose, win, win, win, lo...   
3  [win, lose, lose, win, lose, win, win, win, lo...   
4  [win, win, lose, win, lose, win, lose, lose, l...   
5  [lose, win, win, win, win, lose, win, win, los...   
6  [lose, win, win, win, win, lose, win, win, los...   
7  [win, lose, lose, lose, lose, win, lose, lose,...   
8  [win, lose, lose, lose, lose, win, lose, lose,...   

                               competition_closeness  
0  [Subj 2 Only, Subj 1 Only, Subj 1 Only, Subj 2...  
1  [Subj 2 Only, Subj 1 Only, Subj 1 Only, Subj 2...  
2  [Subj 2 Only, Subj 1 Only, Subj 1 Only, Subj 2...  
3  [Subj 2 Only, Subj 1 Only, Subj 1 Only, Subj 2...  
4  [nan, nan, nan, nan, nan, nan, nan, nan, nan, ...  
5  [Subj 2 blocking Subj 1, Subj 1 Only, Subj 1 t...  
6  [Subj 2 blocking Subj 1, Subj 1 Only, Subj 1 t...  
7  [Subj 2 blocking Subj 1, Subj 1 Only, Subj 1 t...  
8  [Subj 2 blocking Subj 1, Subj 1 Only, Subj 1 t...

In [100]:
grouped_trials_df = grouped_trials_df.drop_duplicates(subset=["recording_file", "current_subject"], keep='first').reset_index(drop=True)

In [101]:
grouped_trials_df

recording_file current_subject  \
0  20230618_100636_standard_comp_to_omission_D2_s...             1.1   
1  20230618_100636_standard_comp_to_omission_D2_s...             1.4   
2  20230619_115321_standard_comp_to_omission_D3_s...             1.4   
3  20230620_114347_standard_comp_to_omission_D4_s...             1.1   
4  20230620_114347_standard_comp_to_omission_D4_s...             1.2   

   video_number                                   time_stamp_index  \
0           1.0  [1099250, 3499256, 5799251, 7599250, 8699250, ...   
1           1.0  [1099250, 3499256, 5799251, 7599250, 8699250, ...   
2           4.0  [1277472, 3577468, 5377470, 6477469, 7477469, ...   
3           1.0  [5757314, 7557336, 8657352, 9657364, 11557385,...   
4           1.0  [5757314, 7557336, 8657352, 9657364, 11557385,...   

                                       trial_outcome  \
0  [lose, win, win, lose, win, lose, lose, lose, ...   
1  [win, lose, lose, win, lose, win, win, win, lo...   
2  [win, win, lose, win, lose, win, lose, lose, l...   
3  [lose, win, win, win, win, lose, win, win, los...   
4  [win, lose, lose, lose, lose, win, lose, lose,...   

                               competition_closeness  
0  [Subj 2 Only, Subj 1 Only, Subj 1 Only, Subj 2...  
1  [Subj 2 Only, Subj 1 Only, Subj 1 Only, Subj 2...  
2  [nan, nan, nan, nan, nan, nan, nan, nan, nan, ...  
3  [Subj 2 blocking Subj 1, Subj 1 Only, Subj 1 t...  
4  [Subj 2 blocking Subj 1, Subj 1 Only, Subj 1 t...

## Seeing which tone time each unit time is closest to

- We will divide all the time up into bins of before and after each tone. Then we will see which time bin the neuron firing falls into.
    - So everything in the 0 bin would be before the first time bin. The 1 bin would be everything in between the first and second time bin. The last would be everything after last time bin.

In [102]:
grouped_trials_df["good_unit_bins"] = grouped_trials_df.apply(lambda x: np.digitize(recording_to_good_unit_times[x["recording_file"]], x["time_stamp_index"], right=True), axis=1)

In [109]:
grouped_trials_df["good_unit_times"] = grouped_trials_df["recording_file"].map(recording_to_good_unit_times)

In [119]:
grouped_trials_df

recording_file current_subject  \
0  20230618_100636_standard_comp_to_omission_D2_s...             1.1   
1  20230618_100636_standard_comp_to_omission_D2_s...             1.4   
2  20230619_115321_standard_comp_to_omission_D3_s...             1.4   
3  20230620_114347_standard_comp_to_omission_D4_s...             1.1   
4  20230620_114347_standard_comp_to_omission_D4_s...             1.2   

   video_number                                   time_stamp_index  \
0           1.0  [1099250, 3499256, 5799251, 7599250, 8699250, ...   
1           1.0  [1099250, 3499256, 5799251, 7599250, 8699250, ...   
2           4.0  [1277472, 3577468, 5377470, 6477469, 7477469, ...   
3           1.0  [5757314, 7557336, 8657352, 9657364, 11557385,...   
4           1.0  [5757314, 7557336, 8657352, 9657364, 11557385,...   

                                       trial_outcome  \
0  [lose, win, win, lose, win, lose, lose, lose, ...   
1  [win, lose, lose, win, lose, win, win, win, lo...   
2  [win, win, lose, win, lose, win, lose, lose, l...   
3  [lose, win, win, win, win, lose, win, win, los...   
4  [win, lose, lose, lose, lose, win, lose, lose,...   

                               competition_closeness  \
0  [Subj 2 Only, Subj 1 Only, Subj 1 Only, Subj 2...   
1  [Subj 2 Only, Subj 1 Only, Subj 1 Only, Subj 2...   
2  [nan, nan, nan, nan, nan, nan, nan, nan, nan, ...   
3  [Subj 2 blocking Subj 1, Subj 1 Only, Subj 1 t...   
4  [Subj 2 blocking Subj 1, Subj 1 Only, Subj 1 t...   

                                      good_unit_bins  \
0  [[0], [0], [0], [0], [0], [0], [0], [0], [0], ...   
1  [[0], [0], [0], [0], [0], [0], [0], [0], [0], ...   
2  [[0], [0], [0], [0], [0], [0], [0], [0], [0], ...   
3  [[0], [0], [0], [0], [0], [0], [0], [0], [0], ...   
4  [[0], [0], [0], [0], [0], [0], [0], [0], [0], ...   

                                     good_unit_times within_interval  
0  [[445], [466], [506], [1224], [1343], [1419], ...              {}  
1  [[937], [998], [1125], [1327], [1346], [1894],...              {}  
2  [[946], [1119], [1148], [1241], [1799], [1976]...              {}  
3  [[160], [483], [535], [868], [1047], [1384], [...              {}  
4  [[120], [262], [439], [632], [723], [919], [93...              {}

- Seeing if the firing time is within a 5 second interval before or 10 second after any tone

In [122]:
grouped_trials_df["good_unit_times"].iloc[0][0][0]

445

In [106]:
from collections import defaultdict

In [126]:
def within_interval(row):
    """
    """
    within_interval_unit_times = defaultdict(list)
    for index, time in enumerate(row['good_unit_times']):
        current_bin = row['good_unit_bins'][index]

        try:
            # checking number before
            first_tone_time = row['time_stamp_index'][current_bin - 1]
            if time >= first_tone_time - 5 * 20000 and time <= first_tone_time + 10 * 20000:
                within_interval_unit_times[first_tone_time].append(
                    (first_tone_time, index, time, row['good_unit_all_ids']))
    
            # checking number after
            second_tone_time = row['time_stamp_index'][current_bin]
            if time >= second_tone_time - 5 * 20000 and time <= second_tone_time + 10 * 20000:
                within_interval_unit_times[second_tone_time].append(
                    (second_tone_time, index, time, row['good_unit_all_ids']))
        except:
            pass
    
    return within_interval_unit_times



In [127]:
grouped_trials_df["within_interval"] = grouped_trials_df.apply(within_interval, axis=1)

In [128]:
grouped_trials_df["within_interval"].iloc[1]

defaultdict(list, {})

In [105]:
within_interval_unit_times = defaultdict(list)
for index, time in enumerate(good_unit_times):
    try:
        current_bin = good_unit_bins[index]


        # checking number before
        first_tone_time = training_and_competition_trials[current_bin - 1]
        if time >= first_tone_time - 5 * 20000 and time <= first_tone_time + 10 * 20000:
            within_interval_unit_times[first_tone_time].append((first_tone_time, index, time, good_unit_all_ids[index]))

        # checking number after
        second_tone_time = training_and_competition_trials[current_bin]
        if time >= second_tone_time - 5 * 20000 and time <= second_tone_time + 10 * 20000:
            within_interval_unit_times[second_tone_time].append((second_tone_time, index, time, good_unit_all_ids[index]))
    except:
        pass

In [106]:
within_interval_unit_times[training_and_competition_trials[0]][:10]

[(1408048, 1915, 1308455, 20),
 (1408048, 1916, 1308605, 20),
 (1408048, 1917, 1309035, 20),
 (1408048, 1918, 1309076, 64),
 (1408048, 1919, 1309948, 54),
 (1408048, 1920, 1310824, 20),
 (1408048, 1921, 1311792, 20),
 (1408048, 1922, 1312528, 20),
 (1408048, 1923, 1312842, 64),
 (1408048, 1924, 1313003, 54)]

In [107]:
within_interval_unit_times[training_and_competition_trials[-1]][:10]

[(60998563, 74962, 60903015, 54),
 (60998563, 74963, 60904506, 54),
 (60998563, 74964, 60904971, 54),
 (60998563, 74965, 60905191, 16),
 (60998563, 74966, 60905737, 54),
 (60998563, 74967, 60906251, 54),
 (60998563, 74968, 60908575, 24),
 (60998563, 74969, 60909269, 20),
 (60998563, 74970, 60910250, 54),
 (60998563, 74971, 60910622, 54)]

## Seeing which 100ms bin each unit time belongs to

- Creating bins for each 100ms time interval

In [108]:
tone_unit_time_to_interval = {}
for time in training_and_competition_trials:
    tone_unit_time_to_interval[time] = [time + num * 2000 for num in range(-50, 100)]

In [109]:
len(tone_unit_time_to_interval[training_and_competition_trials[0]])

150

- Seeing which bin the tone time fits into

In [110]:
all_bin_mapping = None
for key, value in within_interval_unit_times.items():
    unit_fire_time = [fire_time for tone_time, index, fire_time, unit_id in value]
    unit_fire_bin = np.digitize(unit_fire_time, tone_unit_time_to_interval[key], right=True)
    current_tone_bin_map = np.hstack((np.array(value), unit_fire_bin[np.newaxis].T))
    if all_bin_mapping is None:
        all_bin_mapping = current_tone_bin_map
    else: 
        all_bin_mapping = np.vstack((all_bin_mapping, current_tone_bin_map))
    

In [111]:
all_bin_mapping

array([[ 1408048,     1915,  1308455,       20,        1],
       [ 1408048,     1916,  1308605,       20,        1],
       [ 1408048,     1917,  1309035,       20,        1],
       ...,
       [60998563,    75150, 61189530,       54,      146],
       [60998563,    75151, 61194804,       20,      149],
       [60998563,    75152, 61195544,       52,      149]])

## Calculating Firing Rate

In [112]:
from collections import Counter, defaultdict

- Creating a reference for all the tone bin combinations to each tone
    - This is because we need a unique identifier for each tone and bin combination. So we will just add the numbers

In [113]:
tone_bin_for_index = all_bin_mapping[:,0] + all_bin_mapping[:,4]

In [114]:
tone_bin_to_tone = np.hstack((tone_bin_for_index[np.newaxis].T, all_bin_mapping[:,0][np.newaxis].T))

In [115]:
tone_bin_to_tone

array([[ 1408049,  1408048],
       [ 1408049,  1408048],
       [ 1408049,  1408048],
       ...,
       [60998709, 60998563],
       [60998712, 60998563],
       [60998712, 60998563]])

In [116]:
tone_bin_to_tone = dict(zip(tone_bin_to_tone[:,0], tone_bin_to_tone[:,1]))

In [117]:
tone_bin_to_tone

{1408049: 1408048,
 1408050: 1408048,
 1408051: 1408048,
 1408052: 1408048,
 1408053: 1408048,
 1408054: 1408048,
 1408055: 1408048,
 1408056: 1408048,
 1408057: 1408048,
 1408058: 1408048,
 1408059: 1408048,
 1408060: 1408048,
 1408061: 1408048,
 1408062: 1408048,
 1408063: 1408048,
 1408064: 1408048,
 1408065: 1408048,
 1408066: 1408048,
 1408067: 1408048,
 1408068: 1408048,
 1408069: 1408048,
 1408070: 1408048,
 1408071: 1408048,
 1408072: 1408048,
 1408073: 1408048,
 1408074: 1408048,
 1408075: 1408048,
 1408076: 1408048,
 1408077: 1408048,
 1408078: 1408048,
 1408079: 1408048,
 1408080: 1408048,
 1408081: 1408048,
 1408082: 1408048,
 1408083: 1408048,
 1408084: 1408048,
 1408085: 1408048,
 1408086: 1408048,
 1408087: 1408048,
 1408088: 1408048,
 1408089: 1408048,
 1408090: 1408048,
 1408091: 1408048,
 1408092: 1408048,
 1408093: 1408048,
 1408094: 1408048,
 1408095: 1408048,
 1408096: 1408048,
 1408097: 1408048,
 1408098: 1408048,
 1408099: 1408048,
 1408100: 1408048,
 1408101: 14

In [118]:
tone_bin_for_index

array([ 1408049,  1408049,  1408049, ..., 60998709, 60998712, 60998712])

- Getting the number of times each neuron fires

In [119]:
firing_counts = defaultdict(lambda: defaultdict(dict))
for tone_time, index, firing_time, unit_id, bin_index in all_bin_mapping:
    tone_bin = tone_time + bin_index
    if firing_counts[unit_id][tone_bin]:
        firing_counts[unit_id][tone_bin] += 1
    else:
        firing_counts[unit_id][tone_bin] = 1

In [120]:
firing_rate_df = pd.DataFrame.from_dict(firing_counts)

In [121]:
firing_rate_df = firing_rate_df.fillna(value=0)

In [122]:
firing_rate_df.head()

20   64   54   16   52   24
1408049  3.0  1.0  1.0  0.0  0.0  0.0
1408050  2.0  0.0  0.0  0.0  0.0  0.0
1408051  2.0  2.0  2.0  0.0  0.0  0.0
1408052  1.0  1.0  3.0  0.0  0.0  0.0
1408054  1.0  1.0  0.0  0.0  1.0  0.0

In [123]:
firing_rate_df.loc[:].values

array([[3., 1., 1., 0., 0., 0.],
       [2., 0., 0., 0., 0., 0.],
       [2., 2., 2., 0., 0., 0.],
       ...,
       [0., 0., 0., 0., 0., 1.],
       [0., 0., 0., 0., 0., 1.],
       [0., 0., 0., 0., 0., 1.]])

- Classifying each time stamp

In [124]:
all_bin_mapping

array([[ 1408048,     1915,  1308455,       20,        1],
       [ 1408048,     1916,  1308605,       20,        1],
       [ 1408048,     1917,  1309035,       20,        1],
       ...,
       [60998563,    75150, 61189530,       54,      146],
       [60998563,    75151, 61194804,       20,      149],
       [60998563,    75152, 61195544,       52,      149]])

In [125]:
all_bin_mapping[:, 0]

array([ 1408048,  1408048,  1408048, ..., 60998563, 60998563, 60998563])

In [126]:
all_bin_mapping[:, 2]

array([ 1308455,  1308605,  1309035, ..., 61189530, 61194804, 61195544])

- Making a dictionary that maps all the firing times to the corresponding tone

In [127]:
fire_to_tone_time = dict(zip(all_bin_mapping[:, 2], all_bin_mapping[:, 0]))

In [128]:
fire_to_tone_time

{1308455: 1408048,
 1308605: 1408048,
 1309035: 1408048,
 1309076: 1408048,
 1309948: 1408048,
 1310824: 1408048,
 1311792: 1408048,
 1312528: 1408048,
 1312842: 1408048,
 1313003: 1408048,
 1313359: 1408048,
 1313864: 1408048,
 1313972: 1408048,
 1314518: 1408048,
 1315071: 1408048,
 1315342: 1408048,
 1315798: 1408048,
 1315873: 1408048,
 1317171: 1408048,
 1319293: 1408048,
 1319426: 1408048,
 1319739: 1408048,
 1320104: 1408048,
 1323009: 1408048,
 1323620: 1408048,
 1325653: 1408048,
 1325967: 1408048,
 1326267: 1408048,
 1326962: 1408048,
 1327531: 1408048,
 1327774: 1408048,
 1328103: 1408048,
 1331558: 1408048,
 1332596: 1408048,
 1332920: 1408048,
 1333298: 1408048,
 1333728: 1408048,
 1334090: 1408048,
 1336257: 1408048,
 1336328: 1408048,
 1336796: 1408048,
 1337376: 1408048,
 1338688: 1408048,
 1339254: 1408048,
 1339587: 1408048,
 1340532: 1408048,
 1341084: 1408048,
 1341934: 1408048,
 1342577: 1408048,
 1343212: 1408048,
 1343708: 1408048,
 1344039: 1408048,
 1344742: 14

In [129]:
firing_rate_df = firing_rate_df.reset_index()

- Labeling which tone time that fire time belongs to

In [130]:
firing_rate_df["tone_time"] = firing_rate_df["index"].map(tone_bin_to_tone)

In [131]:
firing_rate_df.head()

index   20   64   54   16   52   24  tone_time
0  1408049  3.0  1.0  1.0  0.0  0.0  0.0    1408048
1  1408050  2.0  0.0  0.0  0.0  0.0  0.0    1408048
2  1408051  2.0  2.0  2.0  0.0  0.0  0.0    1408048
3  1408052  1.0  1.0  3.0  0.0  0.0  0.0    1408048
4  1408054  1.0  1.0  0.0  0.0  1.0  0.0    1408048

In [132]:
firing_rate_df["bin"] = firing_rate_df["index"] - firing_rate_df["tone_time"]

In [133]:
training_and_competition_trials

[1408048,
 3008051,
 4808043,
 6408042,
 7908040,
 9908037,
 11808035,
 13608031,
 15208032,
 17008029,
 19008027,
 20808026,
 23208023,
 25008021,
 27998597,
 29598593,
 31398591,
 32998593,
 34498591,
 36498588,
 38398586,
 40198584,
 41798580,
 43598581,
 45598579,
 47398577,
 49798572,
 51598570,
 53298568,
 55098566,
 56998564,
 59398564,
 60998563]

In [134]:
len(training_and_competition_trials)

33

In [ ]:
# iterating through the timestamp of each good unit spike

before_and_after_interval_unit_times = defaultdict(dict)

per_trial_number_of_samples = trial_one_way_duration * sampling_rate

for index, time in enumerate(good_unit_times):
    # getting the corresponding tone bin for the timestamp
    current_bin = good_unit_bins[index]
    current_neuron = good_unit_all_ids[index]   
    
    # checking number before
    first_tone_time = tone_time_stamps[(current_bin - 1) % len(tone_time_stamps)]
    # checking number after
    second_tone_time = tone_time_stamps[(current_bin) % len(tone_time_stamps)]    
    
    # checking if time is before first number
    if first_tone_time - per_trial_number_of_samples <= time <= first_tone_time:
        before_and_after_interval_unit_times[time]["tone_time"] = first_tone_time
        before_and_after_interval_unit_times[time]["before_or_after"] = "before"
        before_and_after_interval_unit_times[time]["neuron_id"] = good_unit_all_ids[index]
    # checking if time is after first number
    elif first_tone_time < time <= first_tone_time + per_trial_number_of_samples:
        before_and_after_interval_unit_times[time]["tone_time"] = first_tone_time
        before_and_after_interval_unit_times[time]["before_or_after"] = "after"
        before_and_after_interval_unit_times[time]["neuron_id"] = good_unit_all_ids[index]
    # checking if time is before second number
    if second_tone_time - per_trial_number_of_samples <= time <= second_tone_time:
        before_and_after_interval_unit_times[time]["tone_time"] = second_tone_time
        before_and_after_interval_unit_times[time]["before_or_after"] = "before"
        before_and_after_interval_unit_times[time]["neuron_id"] = good_unit_all_ids[index]
    # checking if time is after second number
    elif second_tone_time < time <= second_tone_time + per_trial_number_of_samples:
        before_and_after_interval_unit_times[time]["tone_time"] = second_tone_time
        before_and_after_interval_unit_times[time]["before_or_after"] = "after"
        before_and_after_interval_unit_times[time]["neuron_id"] = good_unit_all_ids[index]

In [79]:
recording_to_good_unit_times

{'20230618_100636_standard_comp_to_omission_D2_subj_1_4_t4b3L_box1_merged': array([[     937],
        [     998],
        [    1125],
        ...,
        [67098020],
        [67098467],
        [67098849]]),
 '20230618_100636_standard_comp_to_omission_D2_subj_1_1_t1b2L_box2_merged': array([[     445],
        [     466],
        [     506],
        ...,
        [62445561],
        [62581172],
        [62670994]]),
 '20230620_114347_standard_comp_to_omission_D4_subj_1-1_t1b2L_box_2_merged': array([[     160],
        [     483],
        [     535],
        ...,
        [68361882],
        [68361973],
        [68362204]]),
 '20221122_161341_omission_subject_6_1_top_4_base_2': array([[     106],
        [    1383],
        [    1668],
        ...,
        [27216793],
        [27222475],
        [27223794]]),
 '20230620_114347_standard_comp_to_omission_D4_subj_1-2_t3b3L_box_1_merged': array([[     120],
        [     262],
        [     439],
        ...,
        [68361986],
        [683

<a style='text-decoration:none;line-height:16px;display:flex;color:#5B5B62;padding:10px;justify-content:end;' href='https://deepnote.com?utm_source=created-in-deepnote-cell&projectId=a4490980-3f6a-4f44-80eb-ebd789a5b21f' target="_blank">
 </img>
Created in <span style='font-weight:600;margin-left:4px;'>Deepnote</span></a>